## CNN 1b

### Load Packages

In [10]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
from torch.optim.lr_scheduler import ReduceLROnPlateau
from sklearn.metrics import accuracy_score, f1_score, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns


### Datensatz laden und DatenLoader

In [ ]:


data_path = 'data/embedded_padded'

BATCH_SIZE = 32

train_dataset = torch.load(data_path + '/train.pt')
test_dataset = torch.load(data_path + '/test.pt')
val_dataset = torch.load(data_path + '/val.pt')

# DataLoader vorbereiten


def collate_fn(batch):
    input_ids = torch.stack([item["input_ids"] for item in batch])  
    labels = torch.tensor([item["labels"] for item in batch], dtype=torch.float32).unsqueeze(1)  
    return input_ids, labels

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True, collate_fn=collate_fn)
val_loader = DataLoader(val_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_fn)
test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_fn)


### CNN-Modell definieren


In [ ]:


class HumorCNN(nn.Module):
    def __init__(self, embedding_dim=100):
        super(HumorCNN, self).__init__()

        self.conv1 = nn.Conv2d(1, 50, (3, embedding_dim))
        self.conv2 = nn.Conv2d(1, 50, (4, embedding_dim))
        self.conv3 = nn.Conv2d(1, 50, (5, embedding_dim))

        self.bn1 = nn.BatchNorm1d(50)
        self.bn2 = nn.BatchNorm1d(50)
        self.bn3 = nn.BatchNorm1d(50)

        self.fc = nn.Linear(150, 1)

        self.dropout = nn.Dropout(0.5)
    
    def forward(self, x):
        x = x.unsqueeze(1)  

        x1 = F.relu(self.bn1(self.conv1(x).squeeze(3)))
        x2 = F.relu(self.bn2(self.conv2(x).squeeze(3)))
        x3 = F.relu(self.bn3(self.conv3(x).squeeze(3)))
        
        x1 = F.max_pool1d(x1, x1.size(2)).squeeze(2)
        x2 = F.max_pool1d(x2, x2.size(2)).squeeze(2)
        x3 = F.max_pool1d(x3, x3.size(2)).squeeze(2)

        x = torch.cat((x1, x2, x3), 1)
        
        x = self.dropout(x)
        x = self.fc(x)
        return torch.sigmoid(x)




### Training des Modells


In [ ]:



# Automatische Geräteauswahl (Apple MPS, CUDA, CPU)
if torch.backends.mps.is_available():
    device = torch.device("mps")  
elif torch.cuda.is_available():
    device = torch.device("cuda")  
else:
    device = torch.device("cpu")  

model = HumorCNN().to(device)

criterion = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001, weight_decay=1e-5)  

scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.5, patience=2, verbose=True)  

epochs = 10  # Nur 10 Epochen
best_val_loss = float('inf')
best_test_accuracy = 0
patience = 3
counter = 0

for epoch in range(epochs):
    model.train()
    total_loss = 0

    for texts, labels in train_loader:
        texts, labels = texts.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(texts)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    
    avg_train_loss = total_loss / len(train_loader)

    # ========================
    # Validierung
    # ========================
    model.eval()
    val_loss = 0
    with torch.no_grad():
        for texts, labels in val_loader:
            texts, labels = texts.to(device), labels.to(device)
            outputs = model(texts)
            loss = criterion(outputs, labels)
            val_loss += loss.item()
    
    avg_val_loss = val_loss / len(val_loader)

    # ========================
    # Evaluierung mit Testdaten
    # ========================
    test_preds = []
    test_labels = []
    with torch.no_grad():
        for texts, labels in test_loader:
            texts, labels = texts.to(device), labels.to(device)
            outputs = model(texts)
            predictions = (outputs > 0.5).float()
            test_preds.extend(predictions.cpu().numpy())
            test_labels.extend(labels.cpu().numpy())

    test_accuracy = accuracy_score(test_labels, test_preds)
    test_f1 = f1_score(test_labels, test_preds)

    print(f'Epoch {epoch+1}/{epochs}, Train Loss: {avg_train_loss:.4f}, Val Loss: {avg_val_loss:.4f}, Test Acc: {test_accuracy:.4f}, Test F1: {test_f1:.4f}')
    
    # ========================
    # Lernraten-Anpassung
    # ========================
    scheduler.step(avg_val_loss)

    # ========================
    # Bestes Modell speichern
    # ========================
    if test_accuracy > best_test_accuracy:
        best_test_accuracy = test_accuracy
        torch.save(model.state_dict(), "best_model.pth")
        print("🚀 Bestes Modell gespeichert mit Test-Accuracy:", test_accuracy)

    # ========================
    # Early Stopping
    # ========================
    if avg_val_loss < best_val_loss:
        best_val_loss = avg_val_loss
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print("Early Stopping ausgelöst!")
            break



### Finale Evaluierung & Confusion Matrix



In [ ]:

model.load_state_dict(torch.load("best_model.pth"))  
model.eval()

all_preds = []
all_labels = []

with torch.no_grad():  
    for texts, labels in test_loader:
        texts, labels = texts.to(device), labels.to(device)
        outputs = model(texts)
        predictions = (outputs > 0.5).float()
        all_preds.extend(predictions.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())

all_preds = [int(p[0]) for p in all_preds]
all_labels = [int(l[0]) for l in all_labels]

accuracy = accuracy_score(all_labels, all_preds)
f1 = f1_score(all_labels, all_preds)

print(f'🚀 Finale Test Accuracy: {accuracy:.4f}')
print(f'🚀 Finale Test F1 Score: {f1:.4f}')

# Confusion Matrix
conf_matrix = confusion_matrix(all_labels, all_preds)

plt.figure(figsize=(6,5))
sns.heatmap(conf_matrix, annot=True, fmt='d', cmap="Blues", xticklabels=['No Humor', 'Humor'], yticklabels=['No Humor', 'Humor'])
plt.xlabel("Predicted Label")
plt.ylabel("True Label")
plt.title("Confusion Matrix")
plt.show()
